In [1]:
from fastai.vision.all import *
import os
import pandas as pd
from skimage import io
import matplotlib.pyplot as plt
import numpy as np

import pathlib
from shutil import copyfile

In [2]:
files = get_image_files("classifier_multiobject_v2\\data\\", folders='train')
len(files)

29522

In [3]:
# dictionary of lists 
dict = {'fullnames': files} 
files = pd.DataFrame(dict)
files.head()

fullnames
0  classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1016col1344label21_labelGVD.png
1   classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1016col1344label3_labelGVD.png
2   classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1019col446label25_labelGVD.png
3    classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1019col446label7_labelGVD.png
4  classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1103col1598label23_labelGVD.png

In [4]:
files['basename']=files["fullnames"].apply(lambda x: 
                         os.path.basename(x))
files.head()

fullnames  \
0  classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1016col1344label21_labelGVD.png   
1   classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1016col1344label3_labelGVD.png   
2   classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1019col446label25_labelGVD.png   
3    classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1019col446label7_labelGVD.png   
4  classifier_multiobject_v2\data\train\A21270_ah_1_cell_row1103col1598label23_labelGVD.png   

                                              basename  
0  A21270_ah_1_cell_row1016col1344label21_labelGVD.png  
1   A21270_ah_1_cell_row1016col1344label3_labelGVD.png  
2   A21270_ah_1_cell_row1019col446label25_labelGVD.png  
3    A21270_ah_1_cell_row1019col446label7_labelGVD.png  
4  A21270_ah_1_cell_row1103col1598label23_labelGVD.png

In [5]:
origfile_annos_old = pd.read_csv("classifier_multiobject_v1\\data\\objects_annotations.csv")
origfile_annos_old = origfile_annos_old[["basenames","labels_for_classifier"]]
origfile_additional_annos = pd.read_csv("Data\\additional_GVD_NFT_NCI_single_objects.csv")
origfile_additional_annos["basenames"] = origfile_additional_annos["basenames"].str.replace(".tif",".png",regex=True)
origfile_additional_annos = origfile_additional_annos[["basenames","labels_for_classifier"]]
origfile_annos = pd.concat([origfile_annos_old, origfile_additional_annos])
origfile_annos

basenames  \
0          A21893_ah_1_cell_row106col889label0_labelNormal.png   
1      A21893_ah_1_cell_row1470col699label1640_labelNormal.png   
2        A21893_ah_1_cell_row1501col1968label0_labelNormal.png   
3     A21893_ah_1_cell_row1584col1234label1822_labelNormal.png   
4     A21893_ah_1_cell_row1612col1427label1839_labelNormal.png   
...                                                        ...   
1287         UK2037_ah_3_cell_row962col1568label6_labelGVD.png   
1288     UL1_19_ah_3_cell_row1605col731label1_labelNCI_NFT.png   
1289     UL1_19_ah_3_cell_row1605col731label2_labelNCI_NFT.png   
1290         UL26_09_ah_1_cell_row522col919label1_labelGVD.png   
1291         UL26_09_ah_1_cell_row522col919label2_labelGVD.png   

     labels_for_classifier  
0                   Normal  
1                   Normal  
2                   Normal  
3                   Normal  
4                   Normal  
...                    ...  
1287                   GVD  
1288               NCI_NFT  
1289               NCI_NFT  
1290                   GVD  
1291                   GVD  

[36910 rows x 2 columns]

In [6]:
files = pd.merge(files, origfile_annos, how='right', left_on='basename', right_on='basenames')
files = files.dropna()
files.head()

fullnames  \
0       classifier_multiobject_v2\data\train\A21893_ah_1_cell_row106col889label0_labelNormal.png   
1   classifier_multiobject_v2\data\train\A21893_ah_1_cell_row1470col699label1640_labelNormal.png   
2     classifier_multiobject_v2\data\train\A21893_ah_1_cell_row1501col1968label0_labelNormal.png   
3  classifier_multiobject_v2\data\train\A21893_ah_1_cell_row1584col1234label1822_labelNormal.png   
4  classifier_multiobject_v2\data\train\A21893_ah_1_cell_row1612col1427label1839_labelNormal.png   

                                                   basename  \
0       A21893_ah_1_cell_row106col889label0_labelNormal.png   
1   A21893_ah_1_cell_row1470col699label1640_labelNormal.png   
2     A21893_ah_1_cell_row1501col1968label0_labelNormal.png   
3  A21893_ah_1_cell_row1584col1234label1822_labelNormal.png   
4  A21893_ah_1_cell_row1612col1427label1839_labelNormal.png   

                                                  basenames  \
0       A21893_ah_1_cell_row106col889label0_labelNormal.png   
1   A21893_ah_1_cell_row1470col699label1640_labelNormal.png   
2     A21893_ah_1_cell_row1501col1968label0_labelNormal.png   
3  A21893_ah_1_cell_row1584col1234label1822_labelNormal.png   
4  A21893_ah_1_cell_row1612col1427label1839_labelNormal.png   

  labels_for_classifier  
0                Normal  
1                Normal  
2                Normal  
3                Normal  
4                Normal

In [7]:
files['labels_for_classifier'].value_counts()

labels_for_classifier
Normal     24262
GVD         3095
NCI_NFT     2165
Name: count, dtype: int64

In [8]:
files = files[['basenames','labels_for_classifier']]
files.head()

basenames  \
0       A21893_ah_1_cell_row106col889label0_labelNormal.png   
1   A21893_ah_1_cell_row1470col699label1640_labelNormal.png   
2     A21893_ah_1_cell_row1501col1968label0_labelNormal.png   
3  A21893_ah_1_cell_row1584col1234label1822_labelNormal.png   
4  A21893_ah_1_cell_row1612col1427label1839_labelNormal.png   

  labels_for_classifier  
0                Normal  
1                Normal  
2                Normal  
3                Normal  
4                Normal

In [9]:
#dls = ImageDataLoaders.from_df (files, path='classifier_multiobject_v2\\data\\', valid_pct=0.2, seed=1234,
#                           fn_col='basenames', folder='train', label_col='labels_for_classifier')

In [9]:
#learn = vision_learner(dls, resnet34, metrics=error_rate)
#learn = learn.load('learner')
learn = load_learner(fname='classifier_multiobject_v2\\data\\learner_neuronsubtype.pkl')


In [10]:
#predict on test files
files_1 = get_image_files("classifier_multiobject_v1\\data\\", folders='test')
len(files_1)

7124

In [11]:
#predict on test files
files_2 = get_image_files("classifier_multiobject_v2\\data\\", folders='test')
len(files_2)

256

In [12]:
df_predictions_1 = pd.DataFrame(columns=['Basename','Prediction','Prob_0','Prob_1','Prob_2'])
df_predictions_1

Empty DataFrame
Columns: [Basename, Prediction, Prob_0, Prob_1, Prob_2]
Index: []

In [13]:
for i in range(len(files_1)):
    predictions = learn.predict(files_1[i])
    df_predictions_1.loc[i] = [os.path.basename(files_1[i]),predictions[0],predictions[2].numpy()[0],
                            predictions[2].numpy()[1], predictions[2].numpy()[2] ]

In [14]:
df_predictions_2 = pd.DataFrame(columns=['Basename','Prediction','Prob_0','Prob_1','Prob_2'])
df_predictions_2

Empty DataFrame
Columns: [Basename, Prediction, Prob_0, Prob_1, Prob_2]
Index: []

In [15]:
for i in range(len(files_2)):
    predictions = learn.predict(files_2[i])
    df_predictions_2.loc[i] = [os.path.basename(files_2[i]),predictions[0],predictions[2].numpy()[0],
                            predictions[2].numpy()[1], predictions[2].numpy()[2] ]

In [16]:
df_predictions = pd.concat([df_predictions_1, df_predictions_2])

In [17]:
df_predictions_final = pd.merge(df_predictions, origfile_annos, how='right', left_on='Basename', right_on='basenames')
df_predictions_final = df_predictions_final.dropna()
df_predictions_final

Basename Prediction  \
8      A21893_ah_1_cell_row343col1514label212_labelNormal.png     Normal   
9      A21893_ah_1_cell_row704col1888label613_labelNormal.png     Normal   
13      A21893_ah_1_cell_row903col882label860_labelNormal.png     Normal   
19       A21893_ah_2_cell_row1734col192label0_labelNormal.png     Normal   
32      A21893_ah_3_cell_row326col761label396_labelNormal.png     Normal   
...                                                       ...        ...   
36896       UK2037_ah_2_cell_row675col728label14_labelGVD.png        GVD   
36897        UK2037_ah_2_cell_row675col728label4_labelGVD.png        GVD   
36898       UK2037_ah_2_cell_row875col468label15_labelGVD.png        GVD   
36902      UK2037_ah_3_cell_row1640col1624label2_labelGVD.png        GVD   
36904       UK2037_ah_3_cell_row962col1568label3_labelGVD.png        GVD   

         Prob_0        Prob_1    Prob_2  \
8      0.000449  3.777043e-05  0.999514   
9      0.000284  4.264624e-05  0.999673   
13     0.000014  7.045799e-07  0.999985   
19     0.000515  1.847263e-03  0.997638   
32     0.000070  1.796384e-03  0.998134   
...         ...           ...       ...   
36896  0.999909  2.446646e-05  0.000067   
36897  0.999909  2.446646e-05  0.000067   
36898  0.999988  6.608821e-06  0.000005   
36902  0.999899  9.197348e-06  0.000091   
36904  0.996139  6.214029e-04  0.003240   

                                                    basenames  \
8      A21893_ah_1_cell_row343col1514label212_labelNormal.png   
9      A21893_ah_1_cell_row704col1888label613_labelNormal.png   
13      A21893_ah_1_cell_row903col882label860_labelNormal.png   
19       A21893_ah_2_cell_row1734col192label0_labelNormal.png   
32      A21893_ah_3_cell_row326col761label396_labelNormal.png   
...                                                       ...   
36896       UK2037_ah_2_cell_row675col728label14_labelGVD.png   
36897        UK2037_ah_2_cell_row675col728label4_labelGVD.png   
36898       UK2037_ah_2_cell_row875col468label15_labelGVD.png   
36902      UK2037_ah_3_cell_row1640col1624label2_labelGVD.png   
36904       UK2037_ah_3_cell_row962col1568label3_labelGVD.png   

      labels_for_classifier  
8                    Normal  
9                    Normal  
13                   Normal  
19                   Normal  
32                   Normal  
...                     ...  
36896                   GVD  
36897                   GVD  
36898                   GVD  
36902                   GVD  
36904                   GVD  

[7380 rows x 7 columns]

In [18]:
df_predictions_final = df_predictions_final.drop("basenames", axis=1)
df_predictions_final

Basename Prediction  \
8      A21893_ah_1_cell_row343col1514label212_labelNormal.png     Normal   
9      A21893_ah_1_cell_row704col1888label613_labelNormal.png     Normal   
13      A21893_ah_1_cell_row903col882label860_labelNormal.png     Normal   
19       A21893_ah_2_cell_row1734col192label0_labelNormal.png     Normal   
32      A21893_ah_3_cell_row326col761label396_labelNormal.png     Normal   
...                                                       ...        ...   
36896       UK2037_ah_2_cell_row675col728label14_labelGVD.png        GVD   
36897        UK2037_ah_2_cell_row675col728label4_labelGVD.png        GVD   
36898       UK2037_ah_2_cell_row875col468label15_labelGVD.png        GVD   
36902      UK2037_ah_3_cell_row1640col1624label2_labelGVD.png        GVD   
36904       UK2037_ah_3_cell_row962col1568label3_labelGVD.png        GVD   

         Prob_0        Prob_1    Prob_2 labels_for_classifier  
8      0.000449  3.777043e-05  0.999514                Normal  
9      0.000284  4.264624e-05  0.999673                Normal  
13     0.000014  7.045799e-07  0.999985                Normal  
19     0.000515  1.847263e-03  0.997638                Normal  
32     0.000070  1.796384e-03  0.998134                Normal  
...         ...           ...       ...                   ...  
36896  0.999909  2.446646e-05  0.000067                   GVD  
36897  0.999909  2.446646e-05  0.000067                   GVD  
36898  0.999988  6.608821e-06  0.000005                   GVD  
36902  0.999899  9.197348e-06  0.000091                   GVD  
36904  0.996139  6.214029e-04  0.003240                   GVD  

[7380 rows x 6 columns]

In [19]:
temp = df_predictions_final['labels_for_classifier'].astype(str) + "_" + df_predictions_final['Prediction'].astype(str)
temp.value_counts()

Normal_Normal      6021
GVD_GVD             607
NCI_NFT_NCI_NFT     485
GVD_Normal          112
NCI_NFT_Normal       44
Normal_GVD           43
NCI_NFT_GVD          31
Normal_NCI_NFT       23
GVD_NCI_NFT          14
Name: count, dtype: int64

Index(['Basename', 'Prediction', 'Prob_0', 'Prob_1', 'Prob_2',
       'labels_for_classifier'],
      dtype='object')

8        Normal
9        Normal
13       Normal
19       Normal
32       Normal
          ...  
36896       GVD
36897       GVD
36898       GVD
36902       GVD
36904       GVD
Name: labels_for_classifier, Length: 7380, dtype: object